## Panel app to visualize river network water quality predictions

Demonstrates the use of [`Folium`](https://python-visualization.github.io/folium/) in Panel.

This notebook was based as a response to the [Panel and Folium do they mix](https://discourse.holoviz.org/t/panel-and-folium-do-they-mix/342) question on [Discourse](https://discourse.holoviz.org/).

In [1]:
# originally from https://github.com/MarcSkovMadsen/panel/blob/folium-map/examples/gallery/external/Folium.ipynb

import folium as fm
import pandas as pd
import param
import panel as pn
import random
import geopandas as gpd
pn.extension(loading_spinner='dots', loading_color='#00aa41', sizing_mode="stretch_width")

/data/conda/wqml/lib/python3.10/site-packages/geopandas/_compat.py:112: UserWarning: The Shapely GEOS version (3.11.0-CAPI-1.17.0) is incompatible with the GEOS version PyGEOS was compiled with (3.10.3-CAPI-1.16.1). Conversions between both will be slow.
  warnings.warn(


Download the following dataset and put its content to the folder 'HA':
https://doi.org/10.5285/1957166d-7523-44f4-b279-aa5314163237

In [2]:
HA_gdf = gpd.read_file('HA')
HA_gdf[['HA_NUM','HA_NAME']]
print(HA_gdf.loc[HA_gdf['HA_NUM']==72, 'HA_NAME'].values[0] +': '+ str(72))

Wyre and Lune: 72


You can use `Folium` directly in a Jupyter Notebook

In [3]:
def get_map(lat=52, long=0, zoom_start=5):
    return fm.Map(location=[lat,long], zoom_start=zoom_start)

map = get_map()
#map

But using the `._repr_html_` method on the folium map we can also display it in a Panel `Column`.

In [4]:
def get_map_column(map):
    return pn.Column(
        pn.pane.HTML(map._repr_html_(), sizing_mode="stretch_width"),
        sizing_mode="stretch_width",
    )
#get_map_column(map)

## Interactive Panel app using Folium

Let build an interactive Panel application using Folium.

Lets **define some data**.

In [6]:
def get_df_WQ(season='spring',determinant='nitrate',HA=72,stream_orders=(1,7)):
    predicted = gpd.read_feather('HA72demo/'+determinant+'_'+season+'_predicted.feather')

    str1 = "Predicted_" + determinant.capitalize()
    predicted = predicted.loc[predicted['HA']==HA,["OBJECTID",'LENGTH','STRAHLER', 'SHREVE', 'OS_NAME', 'HA',"geometry",str1]].dropna()
    predicted = predicted.loc[(predicted['STRAHLER'] >= stream_orders[0]) & (predicted['STRAHLER'] <= stream_orders[1])] 

    return predicted
df_WQ = get_df_WQ()
df_WQ.sample(5)

OBJECTID   LENGTH  STRAHLER  SHREVE          OS_NAME  HA  \
157765    309704   840.27       3.0    38.0     River Calder  72   
158805    311981   608.74       2.0     5.0         Un-named  72   
157583    309416  1944.57       3.0    14.0  Westfield Brook  72   
159176    312925    31.14       4.0   125.0     Clough River  72   
157951    310135   813.59       3.0    28.0     River Conder  72   

                                                 geometry  Predicted_Nitrate  
157765  LINESTRING (353311.999 445878.999, 353304.998 ...          -0.131108  
158805  LINESTRING (374595.997 479877.998, 374598.998 ...           0.513455  
157583  LINESTRING (354324.999 437937.998, 354305.999 ...           1.052243  
159176  LINESTRING (370521.000 490931.001, 370498.001 ...           0.069016  
157951  LINESTRING (346530.001 455105.999, 346512.000 ...           0.765275

Lets define some functionality to **add the data to the map** as circles

In [7]:
def add_WQ_lines(map, df_WQ):
    #column=df_WQ.columns[df_WQ.columns.str.startswith('Predicted_')]
    column = df_WQ.columns[df_WQ.columns.str.startswith('Predicted_')][0]
    m = df_WQ.explore(column=column,
        tooltip=column, # show "BoroName" value in tooltip (on hover)
        popup=True, # show all values in popup (on click)
        name='conentration (log10)',
        #style_kwds={'weight':3}, 
        style_kwds={'style_function':lambda x: {"weight": x["properties"]["STRAHLER"]}},
         width = '50%'
        )

    #map.add_child(m)
    #map = m.add_to(map)
    return(m)

#add_WQ_lines(map, df_WQ)
#get_map_column(map)

Lets put it all together into an **interactive app** where the user can select the number of data points to generate and display.

In [10]:

class PanelFoliumMap(param.Parameterized):
    HA = param.Integer(72, bounds=(1,108))
    season = param.Selector(default='spring',objects=['spring','summer','autumn','winter'])
    determinant = param.Selector(default='nitrate',objects=['nitrate','orthophosphate'])
    stream_orders = param.Range(default=(1, 7), bounds=(1,7)) 
    #show = param.Action()
        
    def __init__(self, **params):
        super().__init__(**params)
        
        self.map = get_map()
        self.html_pane = pn.pane.HTML(sizing_mode="stretch_width", min_height=600)    
        self.view = pn.Column(
            pn.Row(self.param.season,self.param.determinant,self.param.HA, self.param.stream_orders ),
            self.html_pane,
            #self.param.show,
            sizing_mode="stretch_width", min_height=600,
        )
        self._update_map()
        self.show = self.show_using_server
    
    @param.depends("HA", "season","determinant",'stream_orders',watch=True)
    def _update_map(self):
        with pn.param.set_values(self.html_pane , loading=True):
            self.map = get_map()
            df_WQ = get_df_WQ(HA=self.HA,determinant=self.determinant, season=self.season, stream_orders=self.stream_orders)
            #add_WQ_lines(self.map, df_WQ)
            if len(df_WQ) > 0:
                self.map = add_WQ_lines(self.map, df_WQ) # return blank map if no reaches
            self.html_pane.object = self.map
            print(HA_gdf.loc[HA_gdf['HA_NUM']==self.HA, 'HA_NAME'].values[0] +': '+ str(self.HA))
        
    def show_using_server(self,_):
        self.view.show()
        
app = PanelFoliumMap()
app.view 

Wyre and Lune: 72


Wyre and Lune: 72 
Wyre and Lune: 72 
Teifi: 62 
Trent: 28 
Norfolk Rivers Group: 34 
Taw and Torridge: 50 
Avon (Bristol): 53 
Usk: 56 
Ystwyth Group: 63 
Dyfi Group: 64 
Glaslyn Group: 65 
Cheshire Rivers Group: 68 
Douglas Group: 70 
Wyre and Lune: 72

Column(min_height=600, sizing_mode='stretch_width')
    [0] Row(sizing_mode='stretch_width')
        [0] Select(name='Season', options=OrderedDict([('spring', ...]), sizing_mode='stretch_width', value='spring')
        [1] Select(name='Determinant', options=OrderedDict([('nitrate', ...]), sizing_mode='stretch_width', value='nitrate')
        [2] IntSlider(end=108, name='HA', sizing_mode='stretch_width', start=1, value=72)
        [3] RangeSlider(end=7, name='Stream orders', sizing_mode='stretch_width', start=1, step=1, value=(1, 7), value_end=7, value_start=1)
    [1] HTML(Map, min_height=600, sizing_mode='stretch_width')

In [9]:
                                                                                description = """

This map shows the results of water quality predictions at UK river reaches using random forest, a machine learning method. The input variables are catchment descriptors and land cover.

Use the controls to select the hydrometric area (HA) to view. You can also select the season, determinant, and filter by stream orders.

You may zoom in and out of the interactive map. Hover or click on the river reach for more details.

```python
@article{wqml,
author = {Tso, Chak‐Hau Michael and Magee, Eugene and Huxley, David and Eastman, Michael and Fry, Matthew},
title = {{Machine Learning Water Quality Predictions at UK River Reaches}}
}
```
"""
pn.template.FastListTemplate(
    site="UKCEH", title="Machine Learning Water Quality Predictions at UK River Reaches", 
    main=[ description, app.view]).servable();

## App

Lets wrap it into nice template that can be served via `panel serve Folium.ipynb`